In [1]:
import glob
from bs4 import BeautifulSoup
from tqdm import tqdm
import sqlite3 as sq
import ast
import json


In [2]:
con = sq.connect("NPOPlayer.db")
cursor = con.cursor()
cursor.execute("CREATE TABLE IF NOT EXISTS NPOPLAYERYN (LINK TEXT PRIMARY KEY, NPOPLAYER int)")
cursor.execute("CREATE TABLE IF NOT EXISTS NPOPLAYER (mediaID TEXT, mainTitle TEXT, broadcaster TEXT, longSummary TEXT, shortSummary TEXT, icons TEXT, subTitle TEXT, thumbnail TEXT, kids TEXT,shareLink TEXT)")
con.commit()


In [3]:


# load html files
files = glob.glob('./data/*.html')
print(files)
data = []

"""
Example from "npo-player-header"
broadcasters='[{"name":"KRO-NCRV","logo":{"url":"https:\/\/www-assets.npo.nl\/uploads\/broadcaster\/46\/logo\/kroncrv-large.png","width":null,"height":null,"alt":""},"url":"http:\/\/www.kro-ncrv.nl"}]' 
franchise-link="https://www.npostart.nl/binnenstebuiten/KN_1676732" 
icons='["leeftijd-al"]' 
kids="false" 
long-summary="Na een lange periode in het buitenland te hebben ge...." 
main-title="BinnensteBuiten" 
media-id="KN_1714711" 
player-id="KN_1714711" 
share-link="https://www.npostart.nl/KN_1714711" 
share-text="Bekijk BinnensteBuiten op https://www.npostart.nl/KN_1714711"
share-title="BinnensteBuiten" 
share-tracking-data='[{"niveau1":"afleveringen","niveau2":"binnenstebuiten","niveau3":"binnenstebuiten"}]' 
sub-title=" 3 jul 2020 19:35 - Seizoen 7 Afl. 40 - BinnensteBuiten" 
summary="Een karakteristiek herenhuis vol buitenlandse herinneringen in Heemstede en Alain Caron helpt mee met de appelpluk in Noord-Holland." 
user-comes-from-outside="true" 
watchlist-tracking-data='[{"name":"kijk_later","type":"action","niveau1":"afleveringen","niveau2":"binnenstebuiten","niveau3":"binnenstebuiten"}]'>
"""



# def dumpfiles(NPOPlayer, notNPOPlayer):
#   with open("notNPOPlayer.txt", "a") as r:
#     r.write(f"{notNPOPlayer}")
#   with open("NPOPlayer.txt", "a") as r:
#     r.write(f"{NPOPlayer}")
#   return "",""



for i, file in enumerate(tqdm((files))):
  if i%1000 ==0:
    con.commit()
  #  NPOPlayer, notNPOPlayer = dumpfiles(NPOPlayer, notNPOPlayer)

  soup = BeautifulSoup(open(file), 'html.parser')
  
  if((header:= soup.find('npo-player-header')) == None):
    cursor.execute(f"INSERT INTO NPOPLAYERYN VALUES ('{file}', 0)")
  else: 
    cursor.execute(f"INSERT INTO NPOPLAYERYN VALUES ('{file}', 1)")
    mediaID = header['media-id']
    mainTitle = header["main-title"]
    try:
      broadCasterName = (json.loads(header["broadcasters"])[0])['name']
    except:
      broadCasterName = "None"
    try:
      icons = ",".join(ast.literal_eval(header['icons']))
    except:
      icons = "None"
    kids = header["kids"]
    shareLink = header["share-link"]
    longSummary = header["long-summary"]
    shortSummary = header["summary"]
    subTitle = header["sub-title"]
    try:
      Thumbnail = json.loads(soup.find("script", attrs={'type':'application/ld+json'}).text.replace("@", ""))['thumbnailUrl']
    except (KeyError, json.JSONDecodeError):
      Thumbnail = ""
    #print(Thumbnail)
    #print(f"{mediaID}','{mainTitle}','{broadCasterName}','{longSummary}','{shortSummary}','{icons}','{subTitle},'{Thumbnail}','{kids}','{shareLink}")
    #cursor.execute("CREATE TABLE IF NOT EXISTS NPOPLAYER (mediaID TEXT PRIMARY KEY, mainTitle TEXT, broadcaster TEXT, longSummary TEXT, shortSummary TEXT, icons TEXT, subTitle TEXT, thumbnail TEXT, kids TEXT,shareLink TEXT)")
    cursor.execute("INSERT INTO NPOPLAYER VALUES (?,?,?,?,?,?,?,?,?,?)", (mediaID, mainTitle, broadCasterName, longSummary, shortSummary, icons,subTitle, Thumbnail, kids, shareLink))
    
    
else:
  #dumpfiles(NPOPlayer, notNPOPlayer)
  con.commit()


['./data\\1-april-hiermee-hou-je-iedereen-voor-de-gek-kinderen-voor-kinderen-blijft-thuis-8-01-04-2020-POMS_BV_16059067.html', './data\\1-auditieronde-1-juniorsongfestivalnl-25-05-2016-POMS_AT_3975232.html', './data\\1-de-boeren-stellen-zich-voor-08-10-2016-KN_1685196.html', './data\\1-de-cactustuin-24-04-2019-WO_KN_15405842.html', './data\\1-dorp-1-postcode-43-miljoen-02-01-2015-BNN_101372385.html', './data\\1-dorp-1-postcode-43-miljoen-POMS_S_BNN_750211.html', './data\\1-euro-per-gesprek-02-02-2022-POW_05260999.html', './data\\1-euro-per-gesprek-03-01-2022-POW_05260990.html', './data\\1-euro-per-gesprek-05-01-2022-POW_05260991.html', './data\\1-euro-per-gesprek-10-01-2022-POW_05260992.html', './data\\1-euro-per-gesprek-12-01-2022-POW_05260993.html', './data\\1-euro-per-gesprek-17-01-2022-POW_05260994.html', './data\\1-euro-per-gesprek-20-01-2022-POW_05260995.html', './data\\1-euro-per-gesprek-24-01-2022-POW_05260996.html', './data\\1-euro-per-gesprek-26-01-2022-POW_05260997.html', '.

100%|██████████| 135271/135271 [2:22:24<00:00, 15.83it/s]  


In [4]:
con.commit()